In [1]:
# import warnings
# warnings.filterwarnings("ignore")

In [2]:
import torch
from torchvision.models.detection import fasterrcnn_resnet50_fpn
from torchvision.transforms import transforms
from torchvision.datasets import CocoDetection
from torch.utils.data import DataLoader
from torch.optim import SGD
from torchvision.models.detection.faster_rcnn import FastRCNNPredictor
#from engine import train_one_epoch, evaluate

import torch
import torchvision
from torchvision.models.detection.faster_rcnn import FastRCNNPredictor
from torchvision.transforms import functional as F
from torch.utils.data import Dataset, DataLoader
import json
import PIL.Image
from matplotlib import pyplot as plt
#train the models on the big dataset with all classes and single faces
import numpy as np
import os
import torch
import time




In [3]:
from face_mask_datasets import MaskDetectionDatasetJSON, MaskDetectionDatasetXML

device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')

CLASS_LABELS_ALL = {
    "empty": 0,
    "mask_colorful": 1,
    "mask_surgical": 2,
    "face_no_mask": 3,
    "face_with_mask_incorrect": 4,
    "face_with_mask": 5,
    "face_other_covering": 6,
    "scarf_bandana": 7,
    "balaclava_ski_mask": 8,
    "face_shield": 9,
    "other": 10,
    "gas_mask": 11,
    "turban": 12,
    "helmet": 13,
    "sunglasses": 14,
    "eyeglasses": 15,
    "hair_net": 16,
    "hat": 17,
    "goggles": 18,
    "hood": 19,
    "hijab_niqab": 20,
}

CLASS_LABELS_FACES = {
    "empty": 0,
    "face_no_mask": 1,
    "face_with_mask_incorrect": 2,
    "face_with_mask": 3,
    "face_other_covering": 4
}

CLASS_LABELS_XML = {
    "empy": 0,
    "without_mask": 1,
    "with_mask": 2,
    "mask_weared_incorrect": 3,
}

TRAIN_PRECENTAGE = 0.8  # 80% of the data is used for training
BATCH_SIZE = 12
NUM_EPOCHS = 10
LEARNING_RATE = 0.005
print("Using device: ", device)

Using device:  cuda


In [4]:
#start a timer
start_time = time.time()

In [5]:
# dataset_big = MaskDetectionDatasetJSON("C:\GIT_Workspaces\Deep-Vision-sta\Datasets\Face Mask Detection Dataset\Medical mask\Medical mask\Medical Mask",CLASS_LABELS, (512,512))
# dataset_big_singleFaces = MaskDetectionDatasetJSON("C:\GIT_Workspaces\Deep-Vision-sta\Datasets\Face Mask Detection Dataset\Medical mask\Medical mask\Medical Mask",CLASS_LABELS,(512,512), only_single_faces=True)
# dataset_big_multipleFaces = MaskDetectionDatasetJSON("C:\GIT_Workspaces\Deep-Vision-sta\Datasets\Face Mask Detection Dataset\Medical mask\Medical mask\Medical Mask",CLASS_LABELS,(512,512), only_multiple_faces=True)

# dataset_small = MaskDetectionDatasetXML("C:\GIT_Workspaces\Deep-Vision-sta\Datasets\Kaggle Face Mask Detection Full",(512,512))
# dataset_small_low_light = MaskDetectionDatasetXML("C:\GIT_Workspaces\Deep-Vision-sta\Datasets\Kaggle Face Mask Detection Full",(512,512), use_dark_images=True)

# #create a dict of the datasets

# datasets = {
#     "dataset_big": dataset_big,
#     "dataset_big_singleFaces": dataset_big_singleFaces,
#     "dataset_big_multipleFaces": dataset_big_multipleFaces,
#     "dataset_small": dataset_small,
#     "dataset_small_low_light": dataset_small_low_light
#}

### Erstellen der Datensätze für den JSON Datensatz mit allen klassen und den Gesicht klassen

In [6]:
dataset_big_all_classes = MaskDetectionDatasetJSON("C:\GIT_Workspaces\Deep-Vision-sta\Datasets\Face Mask Detection Dataset\Medical mask\Medical mask\Medical Mask",CLASS_LABELS_ALL, (512,512))
dataset_big_face_classes = MaskDetectionDatasetJSON("C:\GIT_Workspaces\Deep-Vision-sta\Datasets\Face Mask Detection Dataset\Medical mask\Medical mask\Medical Mask",CLASS_LABELS_FACES,(512,512))

#create a dict of the datasets

datasets = {
    "dataset_big_all_classes": dataset_big_all_classes,
    "dataset_big_face_classes": dataset_big_face_classes
}

dataset init
dataset init


c:\GIT_Workspaces\Deep-Vision-sta\Faster R-CNN\face_mask_datasets.py:62: UserWarning: File 1855.jpg has no annotations
  warnings.warn(f"File {file_name} has no annotations")
c:\GIT_Workspaces\Deep-Vision-sta\Faster R-CNN\face_mask_datasets.py:62: UserWarning: File 1945.jpg has no annotations
  warnings.warn(f"File {file_name} has no annotations")
c:\GIT_Workspaces\Deep-Vision-sta\Faster R-CNN\face_mask_datasets.py:62: UserWarning: File 2135.jpg has no annotations
  warnings.warn(f"File {file_name} has no annotations")
c:\GIT_Workspaces\Deep-Vision-sta\Faster R-CNN\face_mask_datasets.py:62: UserWarning: File 3102.png has no annotations
  warnings.warn(f"File {file_name} has no annotations")
c:\GIT_Workspaces\Deep-Vision-sta\Faster R-CNN\face_mask_datasets.py:62: UserWarning: File 4618.png has no annotations
  warnings.warn(f"File {file_name} has no annotations")
c:\GIT_Workspaces\Deep-Vision-sta\Faster R-CNN\face_mask_datasets.py:62: UserWarning: File 5012.jpg has no annotations
  warn

In [10]:
#create dataloaders for datasets

import torch
from torch.utils.data import Dataset, DataLoader
import utils

dataloaders = {}

for dataset_name, dataset in datasets.items():
    train_size = int(TRAIN_PRECENTAGE * len(dataset))
    test_size = len(dataset) - train_size
    train_dataset, test_dataset = torch.utils.data.random_split(dataset, [train_size, test_size])
    train_dataloader = DataLoader(train_dataset, batch_size=BATCH_SIZE, shuffle=True, collate_fn=utils.collate_fn)
    test_dataloader = DataLoader(test_dataset, batch_size=BATCH_SIZE, shuffle=False, collate_fn=utils.collate_fn)
    dataloaders[dataset_name] = {
        "train": train_dataloader,
        "test": test_dataloader
    }

In [11]:
def getNewModelsClassCompare():
    model_resnet_all_classes = torchvision.models.detection.fasterrcnn_resnet50_fpn(pretrained=True)
    model_resnet_face_classes = torchvision.models.detection.fasterrcnn_resnet50_fpn(pretrained=True)
    model_mobile_all_classes = torchvision.models.detection.fasterrcnn_mobilenet_v3_large_fpn(pretrained=True)
    model_mobile_face_classes = torchvision.models.detection.fasterrcnn_mobilenet_v3_large_fpn(pretrained=True)

    models_classComparison = {
        "resnet":{
            "all_classes": model_resnet_all_classes,
            "face_classes": model_resnet_face_classes
        },
        "mobile":{
            "all_classes": model_mobile_all_classes,
            "face_classes": model_mobile_face_classes
        }
    }
    return models_classComparison

Modelle vorbereiten. Head wird durch einen ersetzt der mnit der neuen Anzahl an klassen übereinstimt

In [12]:
models_classComparison = getNewModelsClassCompare()

num_classes = {
    "all_classes": 21,
    "face_classes": 5
}

#prepare models

for model_name, model_dict in models_classComparison.items():
    for model_type, model in model_dict.items():
        # get number of input features for the classifier
        in_features = model.roi_heads.box_predictor.cls_score.in_features

        # number of classes
        nc = num_classes[model_type]

        # replace the pre-trained head with a new one
        model.roi_heads.box_predictor = FastRCNNPredictor(in_features, nc)

        # move model to the right device
        model.to(device)

c:\Users\johan\.conda\envs\DV-STA\lib\site-packages\torchvision\models\_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
c:\Users\johan\.conda\envs\DV-STA\lib\site-packages\torchvision\models\_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=FasterRCNN_ResNet50_FPN_Weights.COCO_V1`. You can also use `weights=FasterRCNN_ResNet50_FPN_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)
c:\Users\johan\.conda\envs\DV-STA\lib\site-packages\torchvision\models\_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=FasterRCNN_MobileNet_V3_Large_FPN_Weights.COCO_V1`. You 

In [14]:
import copy
from engine import train_one_epoch, evaluate

def train_model(model, dataloaders, optimizer, num_epochs=10):
    """
    This function trains a Model on the given dataloaders for the given number of epochs.
    Dataloaders are expected to be a dict with the keys "train" and "test" and the values are the dataloaders.
    """

    # Define empty arrays to collect metrics
    ap_values = []
    ar_values = []

    losses = []
    for epoch in range(num_epochs):
        # train for one epoch, printing every 10 iterations
        train_one_epoch(model, optimizer, dataloaders["train"], device, epoch, print_freq=1, losses_out=losses)
        # evaluate on the test dataset
        evaluator = evaluate(model, dataloaders["test"], device)

        # Extract the metrics from the evaluator
        average_precisions = evaluator.coco_eval['bbox'].stats[:6]
        average_recalls = evaluator.coco_eval['bbox'].stats[6:]

        # Append the metrics to the arrays
        ap_values.append(average_precisions)
        ar_values.append(average_recalls)

    return model, ap_values, ar_values, losses

## Training der Faster RCNN Modele (mit Resnet und Mobilenet Backbone) auf den Json Datensatz jeweils mit allen klassen und mit den Gesichtsklassen

In [15]:
%matplotlib inline
models_trained = {}

model_type__dataloader_map = {
    "all_classes": "dataset_big_all_classes",
    "face_classes": "dataset_big_face_classes"
}


for model_name, model_dict in models_classComparison.items():
    models_trained[model_name] = {}
    for model_type, model in model_dict.items():

        # if(model_type == "all_classes"):
        #     continue
        
        print("Training model: ", model_name, " ", model_type)
        print("using dataset: ", model_type__dataloader_map[model_type])
        print("--------------------------------------------------")
        params = [p for p in model.parameters() if p.requires_grad]
        optimizer = torch.optim.SGD(params, lr=LEARNING_RATE, momentum=0.9, weight_decay=0.0005)
        model, ap_values, ar_values, losses = train_model(model, dataloaders[model_type__dataloader_map[model_type]], optimizer, num_epochs=NUM_EPOCHS)
        models_trained[model_name][model_type] = model

        # Save the model into the "finished_models" folder
        model_filename = f"{model_name}_{model_type}.pth"
        model_path = os.path.join("finished_models/class_compare/", model_filename)
        torch.save(model.state_dict(), model_path)

        # Save the metrics into the "metric_history" folder
        metric_filename = f"{model_name}_{model_type}_metrics.npz"
        metric_path = os.path.join("finished_models/class_compare/metric_history", metric_filename)
        np.savez(metric_path, ap_values=ap_values, ar_values=ar_values, losses=losses)

        #free memory for next model
        torch.cuda.empty_cache()

        #wait 3 seconds
        print("continue with next model in 3 seconds")
        time.sleep(3)


Training model:  resnet   all_classes
using dataset:  dataset_big_all_classes
--------------------------------------------------
Epoch: [0]  [  0/289]  eta: 0:16:18  lr: 0.000022  loss: 3.5502 (3.5502)  loss_classifier: 3.2139 (3.2139)  loss_box_reg: 0.2440 (0.2440)  loss_objectness: 0.0755 (0.0755)  loss_rpn_box_reg: 0.0168 (0.0168)  time: 3.3872  data: 0.1390  max mem: 8869
Epoch: [0]  [  1/289]  eta: 0:10:35  lr: 0.000040  loss: 3.5502 (3.5683)  loss_classifier: 3.1846 (3.1992)  loss_box_reg: 0.2440 (0.2538)  loss_objectness: 0.0755 (0.0954)  loss_rpn_box_reg: 0.0168 (0.0198)  time: 2.2075  data: 0.2180  max mem: 9028
Epoch: [0]  [  2/289]  eta: 0:08:25  lr: 0.000057  loss: 3.5863 (3.6108)  loss_classifier: 3.2088 (3.2024)  loss_box_reg: 0.2636 (0.2588)  loss_objectness: 0.1153 (0.1280)  loss_rpn_box_reg: 0.0228 (0.0217)  time: 1.7596  data: 0.2043  max mem: 9028
Epoch: [0]  [  3/289]  eta: 0:07:17  lr: 0.000074  loss: 3.5502 (3.5555)  loss_classifier: 3.1846 (3.1915)  loss_box_reg:

## Training der Modelle jeweils auf den hellen und den dunklen XML Datensatz

In [16]:
def getNewModelsLightCompare():
    model_resnet_light = torchvision.models.detection.fasterrcnn_resnet50_fpn(pretrained=True)
    model_resnet_dark = torchvision.models.detection.fasterrcnn_resnet50_fpn(pretrained=True)
    model_mobile_light = torchvision.models.detection.fasterrcnn_mobilenet_v3_large_fpn(pretrained=True)
    model_mobile_dark = torchvision.models.detection.fasterrcnn_mobilenet_v3_large_fpn(pretrained=True)

    models_lightCompare = {
        "resnet":{
            "light": model_resnet_light,
            "dark": model_resnet_dark
        },
        "mobile":{
            "light": model_mobile_light,
            "dark": model_mobile_dark
        }
    }
    return models_lightCompare

In [17]:
models_lightCompare = getNewModelsLightCompare()

for model_name, model_dict in models_lightCompare.items():
    for model_type, model in model_dict.items():
        # get number of input features for the classifier
        in_features = model.roi_heads.box_predictor.cls_score.in_features

        # number of classes
        nc = 4

        # replace the pre-trained head with a new one
        model.roi_heads.box_predictor = FastRCNNPredictor(in_features, nc)

        # move model to the right device
        model.to(device)

dataset_xml_dark = MaskDetectionDatasetXML("C:\GIT_Workspaces\Deep-Vision-sta\Datasets\Kaggle Face Mask Detection Full",CLASS_LABELS_XML,(512,512), use_dark_images=True)
dataset_xml_light = MaskDetectionDatasetXML("C:\GIT_Workspaces\Deep-Vision-sta\Datasets\Kaggle Face Mask Detection Full",CLASS_LABELS_XML,(512,512), use_dark_images=False)

datasets_light = {
    "dataset_xml_dark": dataset_xml_dark,
    "dataset_xml_light": dataset_xml_light
}

dataloaders_light = {}

for dataset_name, dataset in datasets_light.items():
    train_size = int(TRAIN_PRECENTAGE * len(dataset))
    test_size = len(dataset) - train_size
    train_dataset, test_dataset = torch.utils.data.random_split(dataset, [train_size, test_size])
    train_dataloader = DataLoader(train_dataset, batch_size=BATCH_SIZE, shuffle=True, collate_fn=utils.collate_fn)
    test_dataloader = DataLoader(test_dataset, batch_size=BATCH_SIZE, shuffle=False, collate_fn=utils.collate_fn)
    dataloaders_light[dataset_name] = {
        "train": train_dataloader,
        "test": test_dataloader
    }

In [19]:
models_light_trained = {}

model_type__dataloader_map = {
    "light": "dataset_xml_light",
    "dark": "dataset_xml_dark"
}

for model_name, model_dict in models_lightCompare.items():
    models_light_trained[model_name] = {}
    for model_type, model in model_dict.items():
        
        print("Training model: ", model_name, " ", model_type)
        print("using dataset: ", model_type__dataloader_map[model_type])
        print("--------------------------------------------------")
        params = [p for p in model.parameters() if p.requires_grad]
        optimizer = torch.optim.SGD(params, lr=LEARNING_RATE, momentum=0.9, weight_decay=0.0005)
        model, ap_values, ar_values, losses = train_model(model, dataloaders_light[model_type__dataloader_map[model_type]], optimizer, num_epochs=NUM_EPOCHS)
        models_light_trained[model_name][model_type] = model

        # Save the model into the "finished_models" folder
        model_filename = f"{model_name}_{model_type}.pth"
        model_path = os.path.join("finished_models/light_compare/", model_filename)
        torch.save(model.state_dict(), model_path)

        # Save the metrics into the "metric_history" folder
        metric_filename = f"{model_name}_{model_type}_metrics.npz"
        metric_path = os.path.join("finished_models/light_compare/metric_history", metric_filename)
        np.savez(metric_path, ap_values=ap_values, ar_values=ar_values, losses=losses)

        #free memory for next model
        torch.cuda.empty_cache()

        #wait 3 seconds
        print("continue with next model in 3 seconds")
        time.sleep(3)

Training model:  resnet   light
using dataset:  dataset_xml_light
--------------------------------------------------
Epoch: [0]  [ 0/57]  eta: 0:00:48  lr: 0.000094  loss: 1.7714 (1.7714)  loss_classifier: 1.3059 (1.3059)  loss_box_reg: 0.1487 (0.1487)  loss_objectness: 0.2432 (0.2432)  loss_rpn_box_reg: 0.0736 (0.0736)  time: 0.8510  data: 0.1250  max mem: 9807
Epoch: [0]  [ 1/57]  eta: 0:00:42  lr: 0.000183  loss: 1.6228 (1.6971)  loss_classifier: 1.2856 (1.2957)  loss_box_reg: 0.1487 (0.1622)  loss_objectness: 0.1341 (0.1887)  loss_rpn_box_reg: 0.0274 (0.0505)  time: 0.7555  data: 0.1275  max mem: 9966
Epoch: [0]  [ 2/57]  eta: 0:00:39  lr: 0.000273  loss: 1.7714 (1.7376)  loss_classifier: 1.2856 (1.2921)  loss_box_reg: 0.1547 (0.1597)  loss_objectness: 0.2410 (0.2061)  loss_rpn_box_reg: 0.0736 (0.0797)  time: 0.7267  data: 0.1327  max mem: 9967
Epoch: [0]  [ 3/57]  eta: 0:00:38  lr: 0.000362  loss: 1.6228 (1.6982)  loss_classifier: 1.2848 (1.2687)  loss_box_reg: 0.1487 (0.1517)  lo

## Traing der Modelle auf den JSON Datensatz jewils mit nur einzelnen gesichtern

In [20]:
model_single_face_resnet = torchvision.models.detection.fasterrcnn_resnet50_fpn(pretrained=True)
model_single_face_mobile = torchvision.models.detection.fasterrcnn_mobilenet_v3_large_fpn(pretrained=True)

#prepare models

for model in [model_single_face_resnet, model_single_face_mobile]:
    # get number of input features for the classifier
    in_features = model.roi_heads.box_predictor.cls_score.in_features

    # number of classes
    nc = 5

    # replace the pre-trained head with a new one
    model.roi_heads.box_predictor = FastRCNNPredictor(in_features, nc)

    # move model to the right device
    model.to(device)

dataset_single_face = MaskDetectionDatasetJSON("C:\GIT_Workspaces\Deep-Vision-sta\Datasets\Face Mask Detection Dataset\Medical mask\Medical mask\Medical Mask",CLASS_LABELS_FACES,(512,512), only_single_faces=True)
dataset_multiple_face = MaskDetectionDatasetJSON("C:\GIT_Workspaces\Deep-Vision-sta\Datasets\Face Mask Detection Dataset\Medical mask\Medical mask\Medical Mask",CLASS_LABELS_FACES,(512,512), only_multiple_faces=True)

datasets_single_face = {
    "dataset_single_face": dataset_single_face,
    "dataset_multiple_face": dataset_multiple_face
}

dataloaders_crowds = {}

for dataset_name, dataset in datasets_single_face.items():
    train_size = int(TRAIN_PRECENTAGE * len(dataset))
    test_size = len(dataset) - train_size
    train_dataset, test_dataset = torch.utils.data.random_split(dataset, [train_size, test_size])
    train_dataloader = DataLoader(train_dataset, batch_size=BATCH_SIZE, shuffle=True, collate_fn=utils.collate_fn)
    test_dataloader = DataLoader(test_dataset, batch_size=BATCH_SIZE, shuffle=False, collate_fn=utils.collate_fn)
    dataloaders_crowds[dataset_name] = {
        "train": train_dataloader,
        "test": test_dataloader
    }

dataset init
dataset init


In [21]:
single = dataset_single_face.__len__()
multi = dataset_multiple_face.__len__()

print("lenght of single face dataset: ", single, " lenght of multiple face dataset: ", multi)

lenght of single face dataset:  2958  lenght of multiple face dataset:  1356


In [22]:
#train models on single dataset only

models_single_face_trained = {}

for model_name, model in zip(["resnet", "mobile"], [model_single_face_resnet, model_single_face_mobile]):
    models_single_face_trained[model_name] = {}
    for dataset_name, dataloader in dataloaders_crowds.items():
        print("Training model: ", model_name, " ", dataset_name)
        print("--------------------------------------------------")
        params = [p for p in model.parameters() if p.requires_grad]
        optimizer = torch.optim.SGD(params, lr=LEARNING_RATE, momentum=0.9, weight_decay=0.0005)
        model, ap_values, ar_values, losses = train_model(model, dataloader, optimizer, num_epochs=NUM_EPOCHS)
        models_single_face_trained[model_name][dataset_name] = model

        # Save the model into the "finished_models" folder
        model_filename = f"{model_name}_{dataset_name}.pth"
        model_path = os.path.join("finished_models/single_face/", model_filename)
        torch.save(model.state_dict(), model_path)

        # Save the metrics into the "metric_history" folder
        metric_filename = f"{model_name}_{dataset_name}_metrics.npz"
        metric_path = os.path.join("finished_models/single_face/metric_history", metric_filename)
        np.savez(metric_path, ap_values=ap_values, ar_values=ar_values, losses=losses)

        #free memory for next model
        torch.cuda.empty_cache()

        #wait 3 seconds
        print("continue with next model in 3 seconds")
        time.sleep(3)

Training model:  resnet   dataset_single_face
--------------------------------------------------
Epoch: [0]  [  0/198]  eta: 0:03:51  lr: 0.000030  loss: 1.8457 (1.8457)  loss_classifier: 1.6992 (1.6992)  loss_box_reg: 0.1123 (0.1123)  loss_objectness: 0.0267 (0.0267)  loss_rpn_box_reg: 0.0075 (0.0075)  time: 1.1680  data: 0.2840  max mem: 10514
Epoch: [0]  [  1/198]  eta: 0:03:01  lr: 0.000056  loss: 1.8457 (1.8573)  loss_classifier: 1.6992 (1.7072)  loss_box_reg: 0.1123 (0.1199)  loss_objectness: 0.0189 (0.0228)  loss_rpn_box_reg: 0.0074 (0.0075)  time: 0.9215  data: 0.2095  max mem: 10670
Epoch: [0]  [  2/198]  eta: 0:02:44  lr: 0.000081  loss: 1.8457 (1.8284)  loss_classifier: 1.6992 (1.6840)  loss_box_reg: 0.1123 (0.1058)  loss_objectness: 0.0267 (0.0320)  loss_rpn_box_reg: 0.0074 (0.0067)  time: 0.8407  data: 0.1827  max mem: 10672
Epoch: [0]  [  3/198]  eta: 0:02:36  lr: 0.000106  loss: 1.7830 (1.8171)  loss_classifier: 1.6378 (1.6713)  loss_box_reg: 0.1090 (0.1066)  loss_object

In [32]:
import os
import pickle

def save_dataloaders(dataloaders, dataloaders_light, dataloaders_crowds):
    save_folder = "dataloaders"
    os.makedirs(save_folder, exist_ok=True)

    def save_dataloader_dict(dataloader_dict, dict_name):
        dict_folder = os.path.join(save_folder, dict_name)
        os.makedirs(dict_folder, exist_ok=True)

        for dataset_name, dataset_loaders in dataloader_dict.items():
            dataset_folder = os.path.join(dict_folder, dataset_name)
            os.makedirs(dataset_folder, exist_ok=True)

            for split_name, loader in dataset_loaders.items():
                split_folder = os.path.join(dataset_folder, split_name)
                os.makedirs(split_folder, exist_ok=True)

                save_path = os.path.join(split_folder, "dataloader.pkl")
                with open(save_path, "wb") as f:
                    pickle.dump(loader, f)

    save_dataloader_dict(dataloaders, "dataloaders")
    save_dataloader_dict(dataloaders_light, "dataloaders_light")
    save_dataloader_dict(dataloaders_crowds, "dataloaders_crowds")


In [33]:
#save the dataloaders for evaluation purposes

save_dataloaders(dataloaders, dataloaders_light, dataloaders_crowds)

### Speichern der Dataloader. Wenn Modelle später evaluiert werden, dann sollen die gleichen Dataloader verwendet werden.

In [25]:
import pickle

with open('/dataloaders/dataloaders.pickle', 'wb') as handle:
    pickle.dump(dataloaders, handle, protocol=pickle.HIGHEST_PROTOCOL)

{'dataset_big_all_classes': {'train': <torch.utils.data.dataloader.DataLoader at 0x1a7fb31c460>,
  'test': <torch.utils.data.dataloader.DataLoader at 0x1a7fb31c2b0>},
 'dataset_big_face_classes': {'train': <torch.utils.data.dataloader.DataLoader at 0x1a7a6de7790>,
  'test': <torch.utils.data.dataloader.DataLoader at 0x1a7a6de7400>}}